In [ ]:
from collections import defaultdict
from collections import defaultdict, Counter
import requests
import json
import time
from datetime import datetime, timedelta


mes_passado = datetime.now() - timedelta(days=30)
mes_passado_inicio = mes_passado.strftime('%Y-%m-01 00:00:00')
mes_passado_fim = mes_passado.strftime('%Y-%m-31 23:59:59')

data_inicial = '2025-06-01 00:00:00'
data_final = '2025-06-30 23:59:59'

from dotenv import load_dotenv
import os

# Carregar variáveis do .env
load_dotenv()

token = os.getenv('TOKEN_API')

BASE_URL = 'http://10.0.100.128:5009'

In [28]:
def autenticar_whats_ticket():
    try:
        response = requests.post(
            f'{BASE_URL}/auth/login',
            json={
                'email': os.getenv('EMAIL_WHATICKET'),
                'password': os.getenv('SENHA_WHATICKET')
            }
        )
        response.raise_for_status()
        token = response.json().get('token')
        print("✅ Token WhatsTicket obtido com sucesso!")
        return token
    except requests.exceptions.RequestException as e:
        print(f"❌ Erro ao autenticar no WhatsTicket: {e}")
        return None


def enviar_whatsapp(id_fila, mensagem, token):
    if not token:
        print("❌ Token WhatsTicket não disponível.")
        return

    try:
        response = requests.post(
            f'{BASE_URL}/messages/{id_fila}',
            json={'body': mensagem, 'fromMe': True, 'read': 1},
            headers={'Authorization': f'Bearer {token}', 'Content-Type': 'application/json'}
        )
        response.raise_for_status()
        print(f"✅ Mensagem enviada no WhatsApp (fila {id_fila})")
    except requests.exceptions.RequestException as e:
        print(f"❌ Erro ao enviar WhatsApp: {e}")

def filtrar_por_intervalo(registros, inicio, fim):
    return [r for r in registros if inicio <= r['data_criacao'] <= fim]

In [ ]:
# UTILIZANDO PARA COLETAR OS COLABORADORES E IDS DOS MESMO (EXISTENTES)

url = 'https://assinante.nmultifibra.com.br/webservice/v1/funcionarios'

headers = {
    'Authorization': token,
    'Content-Type': 'application/json',
    'ixcsoft': 'listar'
}

body = {
    'qtype': 'funcionarios.id',
    'query': '0',
    'oper': '>',
    'page': '1',
    'rp': '1000',
    'sortname': 'funcionarios.id',
    'sortorder': 'asc'
}

response = requests.post(url, json=body, headers=headers)

if response.status_code == 200:
    data = response.json()
    
    # Iterar diretamente pela lista de registros
    for funcionario in data.get('registros', []):
        print(f"ID: {funcionario.get('id')}, Nome: {funcionario.get('funcionario')}")
else:
    print(f"Erro na requisição: {response.status_code} - {response.text}")

In [ ]:
# FILTRANDO E CONTABILIZANDO A PARTE DE CONTAGEM DE DEMANDAS POR COLABORADORES

headers = {
    'Authorization': token,
    'Content-Type': 'application/json',
    'ixcsoft': 'listar'
}

# --- 1. Buscar colaboradores (técnicos) ---
url_funcionarios = 'https://assinante.nmultifibra.com.br/webservice/v1/funcionarios'
body_funcionarios = {
    'qtype': 'id',
    'query': '0',
    'oper': '>',
    'page': '1',
    'rp': '1000',
    'sortname': 'funcionarios.id',
    'sortorder': 'asc'
}

response_func = requests.post(url_funcionarios, json=body_funcionarios, headers=headers)
tecnicos_info = {}

if response_func.status_code == 200:
    data_func = response_func.json()
    for funcionario in data_func.get('registros', []):
        id_func = int(funcionario.get('id', 0))
        nome_func = funcionario.get('funcionario', 'Nome Desconhecido')
        tecnicos_info[id_func] = nome_func
else:
    print(f"Erro ao buscar colaboradores: {response_func.status_code} - {response_func.text}")
    exit(1)

print(f"Total técnicos carregados: {len(tecnicos_info)}")

# --- 2. Buscar assuntos válidos ---
url_assuntos = 'https://assinante.nmultifibra.com.br/webservice/v1/su_oss_assunto'
body_assuntos = {
    "qtype": "id",
    "query": "0",
    "oper": ">",
    "page": "1",
    "rp": "1000"
}

nomes_assuntos = [
    "Suporte - (SOLUCIONADO) - Sem conexão",
    "Suporte - (SOLUCIONADO) - Quedas de conexão",
    "Suporte - (SOLUCIONADO) - Problemas com softwares",
    "Suporte - (SOLUCIONADO) - Problemas com linha telefônica",
    "Suporte - (SOLUCIONADO) - Liberação de IP válido",
    "Suporte - (SOLUCIONADO) - Lentidão",
    "Suporte - (SOLUCIONADO) - Erro ao acessar sites ou jogos.",
    "Suporte - (SOLUCIONADO) - Alteração de Nome / Senha Wi-Fi",
    "SOLUCIONADO - Roteador Travado / Resetado",
    "Geral - (SOLUCIONADO) - Cancelamento de O.S",
    "TERCEIRIZADA - Validação de O.S Suporte",
    "TERCEIRIZADA - Sem Conexão",
    "TERCEIRIZADA - Problemas na Telefonia Fixa",
    "TERCEIRIZADA - Lentidão",
    "TERCEIRIZADA - Dúvidas de Suporte",
    "TERCEIRIZADA - Solicitação de Alteração de Nome e/ou Senha da Rede Wi-Fi",
    "Ter - OS Sinal fora do padrão",
    "Ter - OS de sem conexão",
    "Ter - OS de quedas",
    "Ter - OS de lentidão",
    "Ter - OS de cabeamento fora do padrão",
    "Configuração de Roteador",
    "Sinal fora do padrão",
    "Troca de equipamento",
    "Vistoria Técnica - NMULTIFIBRA",
    "Retenção",
    "Cabeamento fora do padrão",
    "Transferência de endereço",
    "Mudança de Ponto",
    "Mudança de Ponto - Empresa",
    "ONU Alarmada",
    "Problema de energia (Fonte/ONU)",
    "Quedas de Conexão",
    "Sem Conexão",
    "Lentidão",
    "Suporte - Atualização de Login PPPoE",
    "Suporte - Contato Ativo"
]


response_assuntos = requests.post(url_assuntos, json=body_assuntos, headers=headers)
ids_assuntos_validos = set()
assuntos_dict = {}

if response_assuntos.status_code == 200:
    data_assuntos = response_assuntos.json()
    registros_assuntos = data_assuntos.get('registros', [])
    nomes_assuntos_set = set(nomes_assuntos)

    for assunto in registros_assuntos:
        nome = assunto.get('assunto')
        id_assunto = int(assunto.get('id', 0))
        assuntos_dict[id_assunto] = nome
        if nome in nomes_assuntos_set:
            ids_assuntos_validos.add(id_assunto)
else:
    print(f"Erro ao buscar assuntos: {response_assuntos.status_code} - {response_assuntos.text}")
    exit(1)

# --- 3. Buscar chamados paginados e filtrar ---
url_chamados = 'https://assinante.nmultifibra.com.br/webservice/v1/su_oss_chamado'

ids_tecnicos = [307, 355, 345, 359, 354, 337, 313, 367, 377]

all_chamados = []
page = 1
rp = 1000

while True:
    body_chamados = {
        "qtype": "status",
        "query": "EN",
        "oper": "=",
        "page": str(page),
        "rp": str(rp)
    }

    response_chamados = requests.post(url_chamados, json=body_chamados, headers=headers)

    if response_chamados.status_code != 200:
        print(f"Erro na requisição da página {page}: {response_chamados.status_code} - {response_chamados.text}")
        break

    data_chamados = response_chamados.json()
    registros_chamados = data_chamados.get('registros', [])
    total = int(data_chamados.get('total', 0))

    if not registros_chamados:
        break

    all_chamados.extend(registros_chamados)

    if page * rp >= total:
        break

    page += 1

# --- 4. Filtrar chamados por técnico e assunto válido ---
chamados_filtrados = [
    chamado for chamado in all_chamados
    if int(chamado.get('id_tecnico', 0)) in ids_tecnicos
    and int(chamado.get('id_assunto', 0)) in ids_assuntos_validos
]

# --- 5. Agrupar chamados por técnico e imprimir resumo ---
from collections import defaultdict
chamados_por_tecnico = defaultdict(list)

for chamado in chamados_filtrados:
    id_tec = int(chamado.get('id_tecnico', 0))
    id_assunto = int(chamado.get('id_assunto', 0))
    chamados_por_tecnico[id_tec].append(id_assunto)

for id_tec, assuntos_ids in chamados_por_tecnico.items():
    nome_tec = tecnicos_info.get(id_tec, f"Técnico {id_tec}")
    assuntos_unicos = set(assuntos_ids)
    print(f"ID {id_tec} - {nome_tec}")
    print(f" Tem {len(assuntos_ids)} chamados atribuídos:")
    for assunto_id in assuntos_unicos:
        print(f"- {assuntos_dict.get(assunto_id, f'Assunto {assunto_id}')}")
    print()

whatsapp_token = autenticar_whats_ticket()

mensagem_blocos = []

for id_tec, assuntos_ids in chamados_por_tecnico.items():
    nome_tec = tecnicos_info.get(id_tec, f"Técnico {id_tec}")
    total_chamados = len(assuntos_ids)

    contagem_assuntos = Counter(assuntos_ids)

    bloco = f"Responsável: *{nome_tec}* | Total: *{total_chamados}* chamados\n"
    
    for assunto_id, qtd in contagem_assuntos.items():
        nome_assunto = assuntos_dict.get(assunto_id, f"Assunto {assunto_id}")
        bloco += f"- *{nome_assunto}* : {qtd} chamado{'s' if qtd > 1 else ''}\n"

    mensagem_blocos.append(bloco.strip())  # remove espaço extra do final do bloco

mensagem_geral = "⚠️ Contagem de Demandas Encaminhadas ⚠️\n\n"
mensagem_geral += "\n\n------------------------------\n\n".join(mensagem_blocos)

print("➡️ Enviando mensagem geral:", mensagem_geral)

if whatsapp_token:
    enviar_whatsapp(id_fila=23, mensagem=mensagem_geral, token=whatsapp_token)

In [ ]:
# FILTRANDO E CONTABILIZANDO A PARTE DE CONTAGEM DE DEMANDAS POR COLABORADORES

headers = {
    'Authorization': token,
    'Content-Type': 'application/json',
    'ixcsoft': 'listar'
}

# --- 1. Buscar colaboradores (técnicos) ---
url_funcionarios = 'https://assinante.nmultifibra.com.br/webservice/v1/funcionarios'
body_funcionarios = {
    'qtype': 'id',
    'query': '0',
    'oper': '>',
    'page': '1',
    'rp': '1000',
    'sortname': 'funcionarios.id',
    'sortorder': 'asc'
}

response_func = requests.post(url_funcionarios, json=body_funcionarios, headers=headers)
tecnicos_info = {}

if response_func.status_code == 200:
    data_func = response_func.json()
    for funcionario in data_func.get('registros', []):
        id_func = int(funcionario.get('id', 0))
        nome_func = funcionario.get('funcionario', 'Nome Desconhecido')
        tecnicos_info[id_func] = nome_func
else:
    print(f"Erro ao buscar colaboradores: {response_func.status_code} - {response_func.text}")
    exit(1)

print(f"Total técnicos carregados: {len(tecnicos_info)}")

# --- 2. Buscar assuntos válidos ---
url_assuntos = 'https://assinante.nmultifibra.com.br/webservice/v1/su_oss_assunto'
body_assuntos = {
    "qtype": "id",
    "query": "0",
    "oper": ">",
    "page": "1",
    "rp": "1000"
}

nomes_assuntos = [
    "Suporte - (SOLUCIONADO) - Sem conexão",
    "Suporte - (SOLUCIONADO) - Quedas de conexão",
    "Suporte - (SOLUCIONADO) - Problemas com softwares",
    "Suporte - (SOLUCIONADO) - Problemas com linha telefônica",
    "Suporte - (SOLUCIONADO) - Liberação de IP válido",
    "Suporte - (SOLUCIONADO) - Lentidão",
    "Suporte - (SOLUCIONADO) - Erro ao acessar sites ou jogos.",
    "Suporte - (SOLUCIONADO) - Alteração de Nome / Senha Wi-Fi",
    "SOLUCIONADO - Roteador Travado / Resetado",
    "Geral - (SOLUCIONADO) - Cancelamento de O.S",
    "TERCEIRIZADA - Validação de O.S Suporte",
    "TERCEIRIZADA - Sem Conexão",
    "TERCEIRIZADA - Problemas na Telefonia Fixa",
    "TERCEIRIZADA - Lentidão",
    "TERCEIRIZADA - Dúvidas de Suporte",
    "TERCEIRIZADA - Solicitação de Alteração de Nome e/ou Senha da Rede Wi-Fi",
    "Ter - OS Sinal fora do padrão",
    "Ter - OS de sem conexão",
    "Ter - OS de quedas",
    "Ter - OS de lentidão",
    "Ter - OS de cabeamento fora do padrão",
    "Configuração de Roteador",
    "Sinal fora do padrão",
    "Troca de equipamento",
    "Vistoria Técnica - NMULTIFIBRA",
    "Retenção",
    "Cabeamento fora do padrão",
    "Transferência de endereço",
    "Mudança de Ponto",
    "Mudança de Ponto - Empresa",
    "ONU Alarmada",
    "Problema de energia (Fonte/ONU)",
    "Quedas de Conexão",
    "Sem Conexão",
    "Lentidão",
    "Suporte - Atualização de Login PPPoE",
    "Suporte - Contato Ativo"
]


response_assuntos = requests.post(url_assuntos, json=body_assuntos, headers=headers)
ids_assuntos_validos = set()
assuntos_dict = {}

if response_assuntos.status_code == 200:
    data_assuntos = response_assuntos.json()
    registros_assuntos = data_assuntos.get('registros', [])
    nomes_assuntos_set = set(nomes_assuntos)

    for assunto in registros_assuntos:
        nome = assunto.get('assunto')
        id_assunto = int(assunto.get('id', 0))
        assuntos_dict[id_assunto] = nome
        if nome in nomes_assuntos_set:
            ids_assuntos_validos.add(id_assunto)
else:
    print(f"Erro ao buscar assuntos: {response_assuntos.status_code} - {response_assuntos.text}")
    exit(1)

# --- 3. Buscar chamados paginados e filtrar ---
url_chamados = 'https://assinante.nmultifibra.com.br/webservice/v1/su_oss_chamado'

ids_tecnicos = [307, 355, 345, 359, 354, 337, 313, 367, 377]

all_chamados = []
page = 1
rp = 1000

while True:
    body_chamados = {
        "qtype": "status",
        "query": "EN",
        "oper": "=",
        "page": str(page),
        "rp": str(rp)
    }

    response_chamados = requests.post(url_chamados, json=body_chamados, headers=headers)

    if response_chamados.status_code != 200:
        print(f"Erro na requisição da página {page}: {response_chamados.status_code} - {response_chamados.text}")
        break

    data_chamados = response_chamados.json()
    registros_chamados = data_chamados.get('registros', [])
    total = int(data_chamados.get('total', 0))

    if not registros_chamados:
        break

    all_chamados.extend(registros_chamados)

    if page * rp >= total:
        break

    page += 1

# --- 4. Filtrar chamados por técnico e assunto válido ---
chamados_filtrados = [
    chamado for chamado in all_chamados
    if int(chamado.get('id_tecnico', 0)) in ids_tecnicos
    and int(chamado.get('id_assunto', 0)) in ids_assuntos_validos
]

# --- 5. Agrupar chamados por técnico e imprimir resumo ---
from collections import defaultdict
chamados_por_tecnico = defaultdict(list)

for chamado in chamados_filtrados:
    id_tec = int(chamado.get('id_tecnico', 0))
    id_assunto = int(chamado.get('id_assunto', 0))
    chamados_por_tecnico[id_tec].append(id_assunto)

for id_tec, assuntos_ids in chamados_por_tecnico.items():
    nome_tec = tecnicos_info.get(id_tec, f"Técnico {id_tec}")
    assuntos_unicos = set(assuntos_ids)
    print(f"ID {id_tec} - {nome_tec}")
    print(f" Tem {len(assuntos_ids)} chamados atribuídos:")
    for assunto_id in assuntos_unicos:
        print(f"- {assuntos_dict.get(assunto_id, f'Assunto {assunto_id}')}")
    print()

whatsapp_token = autenticar_whats_ticket()

mensagem_blocos = []

for id_tec, assuntos_ids in chamados_por_tecnico.items():
    nome_tec = tecnicos_info.get(id_tec, f"Técnico {id_tec}")
    total_chamados = len(assuntos_ids)

    contagem_assuntos = Counter(assuntos_ids)

    bloco = f"Responsável: *{nome_tec}* | Total: *{total_chamados}* chamados\n"
    
    for assunto_id, qtd in contagem_assuntos.items():
        nome_assunto = assuntos_dict.get(assunto_id, f"Assunto {assunto_id}")
        bloco += f"- *{nome_assunto}* : {qtd} chamado{'s' if qtd > 1 else ''}\n"

    mensagem_blocos.append(bloco.strip())  # remove espaço extra do final do bloco

mensagem_geral = "⚠️ Contagem de Demandas Encaminhadas ⚠️\n\n"
mensagem_geral += "\n\n------------------------------\n\n".join(mensagem_blocos)

print("➡️ Enviando mensagem geral:", mensagem_geral)

if whatsapp_token:
    enviar_whatsapp(id_fila=23, mensagem=mensagem_geral, token=whatsapp_token)

In [ ]:
# FILTRANDO E CONTABILIZANDO FEEDBACKS EM NOME DOS COLABORADORES (ENCAMINHADOS)

headers = {
    'Authorization': token,
    'Content-Type': 'application/json',
    'ixcsoft': 'listar'
}

# --- 1. Buscar colaboradores (técnicos) ---
url_funcionarios = 'https://assinante.nmultifibra.com.br/webservice/v1/funcionarios'
body_funcionarios = {
    'qtype': 'id',
    'query': '0',
    'oper': '>',
    'page': '1',
    'rp': '1000',
    'sortname': 'funcionarios.id',
    'sortorder': 'asc'
}

response_func = requests.post(url_funcionarios, json=body_funcionarios, headers=headers)
tecnicos_info = {}

if response_func.status_code == 200:
    data_func = response_func.json()
    for funcionario in data_func.get('registros', []):
        id_func = int(funcionario.get('id', 0))
        nome_func = funcionario.get('funcionario', 'Nome Desconhecido')
        tecnicos_info[id_func] = nome_func
else:
    print(f"Erro ao buscar colaboradores: {response_func.status_code} - {response_func.text}")
    exit(1)

print(f"Total técnicos carregados: {len(tecnicos_info)}")

# --- 2. Buscar assuntos válidos ---
url_assuntos = 'https://assinante.nmultifibra.com.br/webservice/v1/su_oss_assunto'
body_assuntos = {
    "qtype": "id",
    "query": "0",
    "oper": ">",
    "page": "1",
    "rp": "1000"
}

nomes_assuntos = [
    "Feedback - Pós BD",
    "Feedback - Pós BD Lógico"
]


response_assuntos = requests.post(url_assuntos, json=body_assuntos, headers=headers)
ids_assuntos_validos = set()
assuntos_dict = {}

if response_assuntos.status_code == 200:
    data_assuntos = response_assuntos.json()
    registros_assuntos = data_assuntos.get('registros', [])
    nomes_assuntos_set = set(nomes_assuntos)

    for assunto in registros_assuntos:
        nome = assunto.get('assunto')
        id_assunto = int(assunto.get('id', 0))
        assuntos_dict[id_assunto] = nome
        if nome in nomes_assuntos_set:
            ids_assuntos_validos.add(id_assunto)
else:
    print(f"Erro ao buscar assuntos: {response_assuntos.status_code} - {response_assuntos.text}")
    exit(1)

# --- 3. Buscar chamados paginados e filtrar ---
url_chamados = 'https://assinante.nmultifibra.com.br/webservice/v1/su_oss_chamado'

ids_tecnicos = [307, 355, 345, 359, 354, 337, 313, 367, 377]

all_chamados = []
page = 1
rp = 1000

while True:
    body_chamados = {
        "qtype": "status",
        "query": "EN",
        "oper": "=",
        "page": str(page),
        "rp": str(rp)
    }

    response_chamados = requests.post(url_chamados, json=body_chamados, headers=headers)

    if response_chamados.status_code != 200:
        print(f"Erro na requisição da página {page}: {response_chamados.status_code} - {response_chamados.text}")
        break

    data_chamados = response_chamados.json()
    registros_chamados = data_chamados.get('registros', [])
    total = int(data_chamados.get('total', 0))

    if not registros_chamados:
        break

    all_chamados.extend(registros_chamados)

    if page * rp >= total:
        break

    page += 1

# --- 4. Filtrar chamados por técnico e assunto válido ---
chamados_filtrados = [
    chamado for chamado in all_chamados
    if int(chamado.get('id_tecnico', 0)) in ids_tecnicos
    and int(chamado.get('id_assunto', 0)) in ids_assuntos_validos
]

# --- 5. Agrupar chamados por técnico e imprimir resumo ---
from collections import defaultdict
chamados_por_tecnico = defaultdict(list)

for chamado in chamados_filtrados:
    id_tec = int(chamado.get('id_tecnico', 0))
    id_assunto = int(chamado.get('id_assunto', 0))
    chamados_por_tecnico[id_tec].append(id_assunto)

for id_tec, assuntos_ids in chamados_por_tecnico.items():
    nome_tec = tecnicos_info.get(id_tec, f"Técnico {id_tec}")
    assuntos_unicos = set(assuntos_ids)
    print(f"ID {id_tec} - {nome_tec}")
    print(f" Tem {len(assuntos_ids)} chamados atribuídos:")
    for assunto_id in assuntos_unicos:
        print(f"- {assuntos_dict.get(assunto_id, f'Assunto {assunto_id}')}")
    print()

whatsapp_token = autenticar_whats_ticket()

mensagem_geral = "⚠️ Contagem de Feedbacks Gerais Distribuidas ⚠️\n\n"

for id_tec, assuntos_ids in chamados_por_tecnico.items():
    nome_tec = tecnicos_info.get(id_tec, f"Técnico {id_tec}")
    total_chamados = len(assuntos_ids)

    # Pegando o nome do primeiro assunto (considerando que todos chamados filtrados são do mesmo tipo por técnico)
    assuntos_unicos = set(assuntos_ids)
    # assuntos_nomes = [assuntos_dict.get(assunto_id, f"Assunto {assunto_id}") for assunto_id in assuntos_unicos]
    # assunto_str = ', '.join(assuntos_nomes)

    mensagem_geral += f"Responsável: *{nome_tec}*\n"
    # mensagem_geral += f"Assunto: *{assunto_str}*\n"
    mensagem_geral += f"Total de Chamados: *{total_chamados}*\n\n"

print("➡️ Enviando mensagem geral:", mensagem_geral)

if whatsapp_token:
    enviar_whatsapp(id_fila=23, mensagem=mensagem_geral, token=whatsapp_token)

# enviar_telegram(mensagem_geral)

In [59]:
# UTILIZANDO PARA FILTRAR E CONSUMIR ATENDIMENTOS POR UMA DATA INICIAL E FINAL

url= 'https://assinante.nmultifibra.com.br/webservice/v1/su_ticket'

headers = {
    'Authorization': token,
    'Content-Type': 'application/json',
    'ixcsoft': 'listar'
}

# Consulta ampla: trazer tudo a partir da data_inicial
body = {
    "qtype": "",
    "query": "",
    "oper": "",
    "page": "1",
    "rp": "1000",
    "grid_param": f"""[{{\"TB\":\"data_criacao\",\"OP\":\">=\",\"P\":\"{mes_passado_inicio}\",\"C\":\"AND\",\"G\":\"data_criacao\"}}, {{\"TB\":\"data_criacao\",\"OP\":\"<=\",\"P\":\"{mes_passado_fim}\",\"C\":\"AND\",\"G\":\"data_criacao\"}}]"""
}

response = requests.post(url, headers=headers, json=body)

if response.status_code == 200:
    resposta_json = response.json()
    
    print("\n===== Resposta Completa da API =====")
    print(json.dumps(resposta_json, indent=4, ensure_ascii=False))

    registros = resposta_json.get('registros', [])

    def filtrar_por_intervalo(registros, inicio, fim):
        return [r for r in registros if inicio <= r['data_criacao'] <= fim]

    #registros_filtrados = filtrar_por_intervalo(registros, data_inicial, data_final)
    registros_filtrados = [r for r in registros if data_inicial <= r['data_criacao'] <= data_final]

    print(f"\n===== Registros filtrados de {data_inicial} até {data_final} =====")
    print(json.dumps(registros_filtrados, indent=4, ensure_ascii=False))
    print(f"Total filtrado: {len(registros_filtrados)}")

else:
    print(f"Erro na requisição: {response.status_code} - {response.text}")



===== Resposta Completa da API =====
{
    "page": "1",
    "total": "24247",
    "registros": [
        {
            "id_resposta": "0",
            "latitude": "",
            "longitude": "",
            "origem_endereco_estrutura": "",
            "id": "1212538",
            "tipo": "C",
            "status_sla": "",
            "id_cliente": "77507",
            "id_assunto": "301",
            "titulo": "Atendimento Chatbot - Erro no Desbloqueio de confianca.",
            "data_criacao": "2025-06-29 23:10:28",
            "data_ultima_alteracao": "2025-06-29 23:10:28",
            "status": "T",
            "su_status": "S",
            "prioridade": "M",
            "id_ticket_setor": "1",
            "mensagens_nao_lida_sup": "0",
            "id_ticket_origem": "",
            "id_usuarios": "0",
            "mensagens_nao_lida_cli": "0",
            "protocolo": "202506171289361",
            "token": "ff7c4850459079b818c6e4c3afccc54c0487a107",
            "id_wfl_process

In [70]:
url = 'https://assinante.nmultifibra.com.br/webservice/v1/su_ticket'

headers = {
    'Authorization': token,
    'Content-Type': 'application/json',
    'ixcsoft': 'listar'
}

# Datas e filtros
mes_passado_inicio = '2025-06-01 00:00:00'
mes_passado_fim = '2025-06-30 23:59:59'

ids_assuntos_desejados = ['9', '100', '345', '246', '101', '11', '201', '331']
ids_tecnicos_esperados = ['355', '345', '359', '354', '337', '313', '367', '377']

# Função para buscar dados paginados
def buscar_todos_registros():
    pagina = 1
    todos_registros = []

    while True:
        body = {
            "qtype": "",
            "query": "",
            "oper": "",
            "page": str(pagina),
            "rp": "1000",
            "grid_param": json.dumps([
                {"TB": "data_criacao", "OP": ">=", "P": mes_passado_inicio, "C": "AND", "G": "data_criacao"},
                {"TB": "data_criacao", "OP": "<=", "P": mes_passado_fim, "C": "AND", "G": "data_criacao"}
            ])
        }

        response = requests.post(url, headers=headers, json=body)
        if response.status_code != 200:
            print(f"Erro na requisição página {pagina}: {response.status_code} - {response.text}")
            break

        dados = response.json()
        registros = dados.get('registros', [])
        total = int(dados.get('total', 0))

        todos_registros.extend(registros)

        print(f"Página {pagina}: {len(registros)} registros obtidos")

        # Se pegou menos que o total esperado, ou zero registros, terminou
        if len(todos_registros) >= total or len(registros) == 0:
            break

        pagina += 1

    return todos_registros

# Buscar todos registros dentro do período
print(f"Buscando registros entre {mes_passado_inicio} e {mes_passado_fim}...")
registros = buscar_todos_registros()

print(f"\nTotal registros brutos retornados: {len(registros)}")

# Filtrar registros por assunto desejado
registros_filtrados_assunto = [
    r for r in registros
    if r.get('id_assunto') in ids_assuntos_desejados
]

print(f"Total registros com assuntos filtrados: {len(registros_filtrados_assunto)}")

# Contar por técnico: total e solucionados
contador = {}
for r in registros_filtrados_assunto:
    id_tec = r.get('id_responsavel_tecnico')
    status = r.get('status', '').strip().upper()
    data_criacao = r.get('data_criacao')

    # Confere data no intervalo (redundante, mas seguro)
    if not (mes_passado_inicio <= data_criacao <= mes_passado_fim):
        continue
    if not id_tec:
        continue

    if id_tec not in contador:
        contador[id_tec] = {'total': 0, 'solucionados': 0}

    contador[id_tec]['total'] += 1
    if status == 'T':
        contador[id_tec]['solucionados'] += 1

tecnicos_presentes = set(contador.keys())

print("\nTécnicos encontrados nos registros:")
print(tecnicos_presentes)

print("\nResumo por técnico (todos encontrados):")
for tec_id in sorted(tecnicos_presentes):
    total = contador[tec_id]['total']
    solu = contador[tec_id]['solucionados']
    print(f"Técnico {tec_id}: Total {total} / Solucionados {solu}")

print("\nResumo para técnicos esperados:")
for tec_id in ids_tecnicos_esperados:
    total = contador.get(tec_id, {}).get('total', 0)
    solu = contador.get(tec_id, {}).get('solucionados', 0)
    print(f"Técnico {tec_id}: Total {total} / Solucionados {solu}")

Buscando registros entre 2025-06-01 00:00:00 e 2025-06-30 23:59:59...
Página 1: 1000 registros obtidos
Página 2: 1000 registros obtidos
Página 3: 1000 registros obtidos
Página 4: 1000 registros obtidos
Página 5: 1000 registros obtidos
Página 6: 1000 registros obtidos
Página 7: 1000 registros obtidos
Página 8: 1000 registros obtidos
Página 9: 1000 registros obtidos
Página 10: 1000 registros obtidos
Página 11: 1000 registros obtidos
Página 12: 1000 registros obtidos
Página 13: 1000 registros obtidos
Página 14: 1000 registros obtidos
Página 15: 1000 registros obtidos
Página 16: 1000 registros obtidos
Página 17: 1000 registros obtidos
Página 18: 1000 registros obtidos
Página 19: 1000 registros obtidos
Página 20: 1000 registros obtidos
Página 21: 1000 registros obtidos
Página 22: 1000 registros obtidos
Página 23: 1000 registros obtidos
Página 24: 1000 registros obtidos
Página 25: 1000 registros obtidos
Página 26: 568 registros obtidos

Total registros brutos retornados: 25568
Total registro